## Format The dataset

In [21]:
from tqdm import tqdm
import json
import pandas as pd
import random
from datasets import Dataset, DatasetDict


with open('/data1/max/telugu_corpus/andhrajyothy_data/andhrajyothy_dataset/all_articles_3months.json', 'r') as f:
    data = json.load(f)


def analyze_headlines(data):
    stories_with_headlines = []
    count_with_headlines = 0
    count_without_headlines = 0
    
    for story in tqdm(data, desc='Filtering Content'):
        has_headlines = False
        story_content = story['content']['StoryContent']
        
        for content in story_content:
            if 'Headlines' in content and content['Headlines']:
                has_headlines = True
                stories_with_headlines.append({
                    'story_id': int(story['story_id']),
                    'headlines': content['Headlines'][0].replace('\u200c', '').replace('\n', '').replace('</p>', '').replace('<p>', '').replace('<b>', '').replace('</b>', ''),
                    'text': content['Body'].replace('\u200c', '').replace('\n', '').replace('</p>', '').replace('<p>', '').replace('<b>', '').replace('</b>', ''),
                })
                
            
    return stories_with_headlines
filtered_data=analyze_headlines(data)


Filtering Content: 100%|██████████| 105218/105218 [00:00<00:00, 125074.19it/s]


In [22]:


def create_huggingface_dataset(corpus_data):
    """
    Create a HuggingFace Dataset from corpus data with combined headlines and text
    
    Args:
        corpus_data (list): List of dictionaries containing story_id, headlines, and text
        
    Returns:
        datasets.Dataset: HuggingFace Dataset object with combined content
    """
    # Create a new list with combined content
    processed_data = []
    for item in corpus_data:
        processed_data.append({
            'story_id': item['story_id'],
            'headline': item['headlines'],
            'article': item['text']
            #'text': f"{item['headlines']}\n\n{item['text']}"  # Combining headlines and text with double newline
        })
    
    # Convert to DataFrame
    df = pd.DataFrame(processed_data)
    
    # Create HuggingFace Dataset
    dataset = Dataset.from_pandas(df)
    
    return dataset



# Create the dataset
train_dataset = create_huggingface_dataset(filtered_data)
# Print first example to show combined content
print("\nFirst example:")
print(train_dataset[0])

print('Length of the train dataset',len(train_dataset))


# # Save the dataset (optional)
# dataset.save_to_disk("telugu_news_dataset")


First example:
{'story_id': 2481002, 'headline': 'బుమ్రాకు విశ్రాంతి!', 'article': 'కుల్దీప్–అక్షర్ మధ్య పోటీ27 నుంచి బంగ్లాతో రెండో టెస్టున్యూఢిల్లీ: వరల్డ్ టెస్టు చాంపియన్షిప్ (డబ్ల్యూటీసీ) 2023–25 అంచెలో భాగంగా టీమిండియా ఆడే పది టెస్టుల్లో మొదటిదాన్ని ఘన విజయంతో ముగించింది. బంగ్లాదేశ్తో జరిగిన ఈ మ్యాచ్లో ఏకంగా 280 పరుగుల తేడాతో నెగ్గి డబ్ల్యూటీసీ టేబుల్లో తమ అగ్రస్థానాన్ని మరింత పదిలపర్చుకుంది. ఇక శుక్రవారం నుంచి కాన్పూర్లో చివరిదైన రెండో టెస్టు జరుగుతుంది. వాస్తవానికి ఈ పది టెస్టుల్లో రోహిత్ సేన సగం మ్యాచ్లను గెలిచినా ఫైనల్లో చోటు ఖాయమే. బంగ్లాతో రెండో టెస్టు తర్వాత స్వదేశంలో కివీస్తో మూడు టెస్టులు ఉంటాయి. ఆ తర్వాత ఐదు టెస్టుల సిరీస్ కోసం భారత జట్టు ఆస్ట్రేలియా టూర్కు వెళ్లాల్సి ఉంటుంది. అయితే అక్కడ ఆత్మవిశ్వాసంతో సిరీస్ను ఆరంభించేందుకు, సొంత గడ్డపై మిగిలిన మూడు టెస్టులను గెలిచి ఒత్తిడి తగ్గించుకోవాలనుకుంటోంది.కాన్పూర్ పిచ్ను అనుసరించి ముగ్గురు స్పిన్నర్లతో వెళ్లాలనుకుంటే జట్టుకు ఓ పేసర్ దూరం కావాల్సిందే. ఒకవేళ బుమ్రాకు రెస్ట్ ఇస్తే ఇబ్బంది లేదు. కానీ తను ఆడితే మరో పేసర్ ఆకాశ్ దీప

## Append the TeClass dataset as validation set

We are only considering HREL content for validation of current dataset

In [23]:

te_df = pd.read_csv('/data1/max/telugu_corpus/TeClass_training_data.csv')
filtered_df = te_df[te_df['label'] == 'HREL']

In [27]:


def create_huggingface_dataset(filtered_df):
    """
    Create a HuggingFace Dataset from corpus data with combined headlines and text
    
    Args:
        filtered_df (data frame)): dataframe for valset
        
    Returns:
        datasets.Dataset: HuggingFace Dataset object with combined content
    """
    # Create a new list with combined content
    processed_data = []
    for i,item in filtered_df.iterrows():
        processed_data.append({
            'story_id': random.randint(100000,999999),
            'headline': item['headline'],
            'article': item['article']  # Combining headlines and text with double newline
        })
    
    # Convert to DataFrame
    df = pd.DataFrame(processed_data)
    
    # Create HuggingFace Dataset
    dataset = Dataset.from_pandas(df)
    
    return dataset



# Create the dataset
val_dataset = create_huggingface_dataset(filtered_df)
# Print first example to show combined content
print("\nFirst val example:")
print(val_dataset[0])


First val example:
{'story_id': 920427, 'headline': 'శేఖర్ కమ్ముల తండ్రి శేషయ్య కన్నుమూత', 'article': 'ప్రముఖ దర్శకులు శేఖర్ కమ్ముల ఇంట విషాదం నెలకొంది . ఆయన తండ్రి కమ్ముల శేషయ్య ( 89 ) కన్నుమూశారు . ఆయన గత కొద్దికాలంగా వృద్దాప్య సంబంధింత సమస్యలతో బాధపడుతున్నారు . ప్రస్తుత పరిస్థితుల్లో కొద్దికాలంగా ఇంటి వద్దే చికిత్స అందిస్తున్నారు . ఇటీవల ఆరోగ్యం క్షీణించడంతో స్థానిక ప్రైవేట్ హాస్పిటల్లో చేర్పించారు . అక్కడే చికిత్స పొందుతూ శనివారం ఉదయం 6 గంటలకు మరణించారు అని సన్నిహితులు తెలిపారు . శనివారం సాయంత్రం బన్సీలాల్ పేట స్మశాన వాటికలో అంత్యక్రియలు జరుగుతాయని కుటుంబ సభ్యులు తెలిపారు . శేఖర్ కమ్ముల లాక్డౌన్ సమయంలో కరోనా వారియర్స్తో మాట్లాడుతూ ప్లాస్మా దానం చేయాలని అవగాహన కల్పిస్తున్నారు . ఇక సినిమాల విషయానికి వస్తే .. నాగచైతన్య , సాయిపల్లవి హీరోహీరోయిన్లుగా ‘లవ్స్టోరి’ సినిమాను తెరకెక్కిస్తున్నారు శేఖర్ కమ్ముల . ఈ సినిమా షూటింగ్ తుది దశకు చేరుకుంది . సినీ రంగానికి చెందిన పలువురు సోషల్ మీడియా ద్వారా సంతాపం వ్యక్తం చేశారు .'}


In [28]:

dataset  = DatasetDict({'train': train_dataset, 'validation': val_dataset})

Push to the hub for future use

In [32]:
import os



dataset.push_to_hub("saidines12/telugu_news_dataset")

Uploading the dataset shards: 100%|██████████| 1/1 [00:03<00:00,  3.18s/it]


CommitInfo(commit_url='https://huggingface.co/datasets/saidines12/telugu_news_dataset/commit/724a92685e7e0a2959cee47d6c7f8b8a74573d59', commit_message='Upload dataset', commit_description='', oid='724a92685e7e0a2959cee47d6c7f8b8a74573d59', pr_url=None, pr_revision=None, pr_num=None)